<a href="https://colab.research.google.com/github/ToAN7/SIC_AI/blob/TrongKha_/SIC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [18]:
!pip install sentence_transformers

  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_curand_cu12-10.3.2.106-py3-none-manylinux1_x86_64.whl.metadata (1.5 kB)
  Using cached nvidia_cusolver_cu12-11.4.5.107-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_cusparse_cu12-12.1.0.106-py3-none-manylinux1_x86_64.whl.metadata (1.6 kB)
  Using cached nvidia_nccl_cu12-2.20.5-py3-none-manylinux2014_x86_64.whl.metadata (1.8 kB)
  Using cached nvidia_nvtx_cu12-12.1.105-py3-none-manylinu

In [19]:
from sentence_transformers import SentenceTransformer

/usr/local/lib/python3.10/dist-packages/sentence_transformers/cross_encoder/CrossEncoder.py:11: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


#import thư viện

In [2]:
from sklearn.svm import SVR# mô hình chạy thử
from sklearn.svm import SVC# mô hình chạy thử
from sklearn.neighbors import KNeighborsClassifier# mô hình chạy thử
import pandas as pd# lấy dữ liệu
import numpy as np # tính toán
import matplotlib.pyplot as plt # vẽ đồ thị
# from sentence_transformers import SentenceTransformer # Doc2Vec với dữ liệu dùng để kiểm thử
from sklearn.cluster import KMeans # Clustering
from sklearn.model_selection import train_test_split # Chia dữ liệu
from sklearn.model_selection import cross_val_score, KFold # đánh giá mô hình
from sklearn.metrics import classification_report, accuracy_score, confusion_matrix #đánh giá mô hình
import re # tiền xử lý
import string # tiền xử lý
from sklearn.decomposition import PCA # giảm chiều dữ liệu
from scipy.spatial.distance import pdist, squareform # Tìm tâm cụm
from sklearn.metrics.pairwise import euclidean_distances #tính khoảng cách đầu vào và so sánh với tâm cụm
from sklearn.svm import OneClassSVM # Phân loại
from sklearn.feature_extraction.text import TfidfVectorizer # Tính tfidf
import joblib
import warnings # ngăn cảnh báo vô hại
from sklearn.metrics.pairwise import cosine_similarity#Tính độ đo cosine cho ebd

#Hàm

In [3]:
vietnamese_stop_words = [
              'là', 'và', 'có', 'trên', 'cho', 'một', 'các', 'được', 'như', 'với',
              'của', 'ở', 'khi', 'đã', 'còn', 'thì', 'này', 'bởi', 'đó', 'để', 'năm',
              'ngày', 'vào', 'sau', 'tại', 'trong', 'rằng', 'đến', 'từ'
              ]

In [4]:
pca = PCA(n_components=2)

In [20]:
model = SentenceTransformer('/content/drive/MyDrive/SIC/model_doc2vec')

In [6]:
model_kmeans = joblib.load('/content/drive/MyDrive/SIC/kmeans_model.pkl')

In [7]:
#Hàm làm sạch dữ liệu <nên dùng trước khi vector hoá dữ liệu>
def convertData(text):
  text = text.lower()
  text = re.sub('\[.*?\]','',text)
  text = re.sub("\\W"," ",text)
  text = re.sub('https?://\S+|www\.\S+','',text)
  text = re.sub('<.*?>+',b'',text)
  text = re.sub('[%s]' % re.escape(string.punctuation),'',text)
  text = re.sub('\w*\d\w*','',text)
  text = re.sub(' +', ' ',text)
  text = text.strip()
  text = ' '.join([word for word in text.split() if word not in vietnamese_stop_words])
  return text

<h2>Cosine_similarity

In [8]:
# # #Hàm tính độ đo cosine
# # def cosine_similarity(x_vec,y_vec):
# #   cosine_similarities = []
# #   for i in range(x_vec.shape[0]):
# #     cos_sim = (x_vec[i] * y_vec.T).toarray().squeeze()
# #     cosine_similarities.append(cos_sim)
# #   return cosine_similarities

def cosine_similarity_1(x_vec,y_vec, flag):
  cosine_similarities = x_vec.dot(y_vec.T)
  if flag == True:
    return cosine_similarities.toarray().squeeze()#
  else:
    ll = []
    for i in range(cosine_similarities.shape[0]):
      ll.append(cosine_similarities[i].max())
    return ll
    # return cosine_similarities

In [9]:
#Hàm kiểm thử cho đánh giá độ tương đồng Cosine
def Cosine_sml(lt, data_test, len_real,real_vectors):#data_test và len_real là list:8943
  for i in range(len(data_test)):
    content = [convertData(txt) for txt in data_test[i]['Fake_Content']]
    print(content)
    vectors_content = vectorizer.transform(content)
    cosine_similarities = cosine_similarity(vectors_content,real_vectors, True)
    danhgia_f = 0
    for idx, x in enumerate(cosine_similarities):
      if x.max() < 0.5:
        danhgia_f +=1


    print(f'Tổng số tin giả của data_test{i} : {len(data_test[i])}')
    print(f'Số lượng tin được phát hiện có khả năng là giả của data_test{i}: {danhgia_f}')
    print(f"Độ chính xác khi dự đoán tin giả : {danhgia_f/len(data_test[i])}")
    lt.append(danhgia_f/len(data_test[i]))
    print('_____________________________________________________________________________________')
  return lt

In [10]:
#Hàm kiểm thử cho đánh giá độ tương đồng Cosine
def Cosine_sml_ebd(lt,fake_vectors,real_vectors):#fake_vectors va real_vectors
  cosine_similarities = cosine_similarity(fake_vectors,real_vectors, False)
  danhgia_f = 0
  # print(cosine_similarities.shape)
  # print(cosine_similarities[0])
  all = []
  num = []
  for idx, x in enumerate(cosine_similarities):
    if x.max() < 0.5:
      danhgia_f +=1
      all.append(x.max())
    else:
      num.append(x.max())
  print(num)
  print(all)
  print(f'Tổng số tin giả của fake_ : {len(fake_vectors)}')
  print(f'Số lượng tin được phát hiện có khả năng là giả của fake_: {danhgia_f}')
  print(f"Độ chính xác khi dự đoán tin giả : {danhgia_f/len(fake_vectors)}")
  lt.append(danhgia_f/len(fake_vectors))
  print('_____________________________________________________________________________________')
  return lt

#Gọi dữ liệu test

In [11]:
#Tập dữ liệu gốc ~ dùng với độ đo cosine
real_news = pd.read_csv('/content/drive/MyDrive/Data_/Data_test_300/DATA_.csv')#Tập tin có thể là thật
real_news.drop(columns=['Unnamed: 0'],inplace=True)
# real_news.columns = ['Content']
real_news = real_news[4000:]
real_news.reset_index(inplace=True)
real_news.drop(columns=['index'],inplace=True)
teptingia = pd.read_csv('/content/drive/MyDrive/Data_/dulieutin_gia_4000.csv')#Tập tin có thể là giả
teptingia.drop(columns=['Unnamed: 0'],inplace=True)
# teptingia.columns = ['Content']
teptingia.reset_index(inplace=True)
teptingia.drop(columns=['Unnamed: 0.1'],inplace=True)
teptingia.drop(columns=['index'],inplace=True)
ebd_teptingia = pd.read_csv('/content/drive/MyDrive/Data_/Fake_Ebd_4000.csv') # 4000 dữ liệu đầu tiên
ebd_teptinthat = pd.read_csv('/content/drive/MyDrive/SIC/Embeddings_DATA.csv')
ebd_teptinthat.drop(columns=['Unnamed: 0'],inplace=True)
ebd_teptingia.drop(columns=['Unnamed: 0'],inplace=True)
ebd_teptinthat = ebd_teptinthat[4000:]
ebd_teptinthat.reset_index(inplace=True)
ebd_teptinthat.drop(columns=['index'],inplace=True)

#Độ tương đồng Cosine

<h1>TfIDF</h1>

In [ ]:
vectorizer = TfidfVectorizer()
real_vectors = vectorizer.fit_transform(real_news['Content'])

In [ ]:
lt = list()# để lưu kết quả test
lt_km = list()
lit = []
lit.append(len(real_news))

In [ ]:
Cosine_sml(lt,[teptingia],[len(real_news)],real_vectors)#tfidf

['vượt lên những nghi lễ ngoại giao tổng bí thư nguyễn phú trọng thể hiện hình ảnh sống động phẩm giá cốt cách việt nam sự hiểu lầm lớn', 'cuộc sống đời thường hoạt động cách mạng minh chứng rõ nét nhất về việc hiện thực hóa lý tưởng đạo đức cách mạng mà tổng bí thư nguyễn phú trọng theo đuổi sự hiểu lầm lớn', 'nhà thờ dòng họ nguyễn phú nằm khép mình con ngõ nhỏ thuộc xóm làng lại đà bình dị mộc mạc nhuốm màu thời gian không đáng tin cậy', 'tổng bí thư nguyễn phú trọng con người luôn luôn nghĩ chuyện làm lợi ích người khác ẩn con người chất thép người cộng sản không đáng tin cậy', 'hôm nay sở gd đt tp hcm công bố danh sách trường thpt xét tuyển bổ sung lớp công lập học hoàn toàn sai lầm', 'bảo hiểm xã hội bhxh việt nam vừa ban hành công văn về việc thông tin giả mạo văn bản đơn vị bị bóp méo hoàn toàn', 'ứng phó bão số thủ tướng đề nghị theo dõi chặt chẽ diễn biến bão rà soát chủ động sơ tán người dân ra khỏi khu vực nguy hiểm bị thổi phồng quá mức', 'vị trí sạt lở khiến người thương 

[0.5425]

In [ ]:
cosine_sim = cosine_similarity(ebd_teptinthat, ebd_teptingia)
dem = 0
for i in cosine_sim:
  if i.all() > 0.5:
    dem+=1
print(dem/len(cosine_sim))

1.0


<h1>Bert</h1>

In [ ]:
Cosine_sml_ebd(lt,ebd_teptingia,ebd_teptinthat)

[0.514134921616461, 0.5860062107638382, 0.6285483651739809, 0.7181767086214674, 0.5251513982966465, 0.544016599164422, 0.512468821301011, 0.5531637202169999, 0.5175755914554971, 0.6582955146125473, 0.5892055411174824, 0.7146937288859909, 0.7390622826419534, 0.643695086845115, 0.7679959009020203, 0.6018339560574307, 0.7871098841414945, 0.6074002568716794, 0.6569814902928961, 0.6179092592653626, 0.5762066984767296, 0.6480693210543849, 0.750525928771512, 0.622102988719361, 0.6915707550000763, 0.5775241834177771, 0.6409057784485507, 0.6310485542127079, 0.6716561929398992, 0.6934330355206768, 0.5109545458358672, 0.612643824795955, 0.7993709756133109, 0.7238722720402537, 0.5253639380978965, 0.6592731219658301, 0.7231896424660613, 0.6521735994790993, 0.6227887858317631, 0.5812667621520713, 0.5233091942648918, 0.5723463259836902, 0.7900498303212252, 0.6615735095456176, 0.688564590616463, 0.5665993232392347, 0.7004262153969774, 0.7236416333565882, 0.6276217093641407, 0.7049881815835528, 0.62034

[0.5425, 0.0455]

#Sử dụng tfIdf để vector hoá

SVM_SVC

In [12]:
svc_model = joblib.load('/content/drive/MyDrive/SIC/svc_model_update.pkl')

In [13]:
X_Fake_tfidf = [convertData(teptingia['Fake_Content'][i]) for i in range(len(teptingia['Fake_Content']))]
X_Real_tfidf = [convertData(real_news['Content'][i]) for i in range(len(real_news['Content']))]

In [ ]:
X = X_Real_tfidf + X_Fake_tfidf
Y = [1]*len(X_Real_tfidf) + [0]*len(X_Fake_tfidf)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.2, random_state=42)

In [14]:
vectorizer = TfidfVectorizer()#max_features=5000
X_train_tfidf = vectorizer.fit_transform(X_train)
X_test_tfidf = vectorizer.transform(X_test)
#bert sentence_transformer

NameError: name 'X_train' is not defined

In [ ]:
len(X_train)

7154

In [ ]:
len(y_test)

1789

In [16]:
vectorizer = TfidfVectorizer()#max_features=5000
txt = 'Không vì đẩy mạnh chống tham nhũng mà cản trở phát triển kinh tế'
txt_p = convertData(txt)
txt_p = vectorizer.fit_transform([txt_p])

In [17]:
print(svc_model.predict(txt_p))

ValueError: X has 14 features, but SVC is expecting 29728 features as input.

In [ ]:
y_pred = svc_model.predict(X_test_tfidf)
#kiểm tra X_test_tfidf
# Calculate the accuracy of the model.
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy: {:.2f}%".format(accuracy * 100))
# Display the classification report and confusion matrix.
print("Classification Report:")
print(classification_report(y_test, y_pred))
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

Accuracy: 78.42%
Classification Report:
              precision    recall  f1-score   support

           0       0.75      0.79      0.77       819
           1       0.82      0.78      0.80       970

    accuracy                           0.78      1789
   macro avg       0.78      0.79      0.78      1789
weighted avg       0.79      0.78      0.78      1789

Confusion Matrix:
[[651 168]
 [218 752]]


KNN

In [ ]:
import joblib
from joblib import load as ld
knn_model = ld('/content/drive/MyDrive/SIC/knn_model_Update.joblib')

In [ ]:
y_pred = knn_model.predict(X_test_tfidf)
# Calculate the accuracy of the model.
accuracy = accuracy_score(y_test, y_pred)
print("Accuracy: {:.2f}%".format(accuracy * 100))
# Display the classification report and confusion matrix.
print("Classification Report:")
print(classification_report(y_test, y_pred))
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))
#bỏ KMeans

Accuracy: 61.93%
Classification Report:
              precision    recall  f1-score   support

           0       0.59      0.56      0.57       819
           1       0.64      0.67      0.66       970

    accuracy                           0.62      1789
   macro avg       0.62      0.61      0.61      1789
weighted avg       0.62      0.62      0.62      1789

Confusion Matrix:
[[459 360]
 [321 649]]


#Sử dụng bert để vector hoá

In [21]:
svc_model_ebd = joblib.load('/content/drive/MyDrive/SIC/svc_model_ebd.pkl')

In [47]:
txt = input()

Công an TP.HCM: Thu thập thông tin người mua bán vàng nhằm ngăn chặn việc đầu cơ Báo Người Lao Động đưa tin, chiều 1/8, UBND TP.HCM tổ chức họp báo tình hình kinh tế - xã hội trên địa bàn. Tại buổi họp báo, đại diện Công an TP.HCM đã thông tin về việc thu thập thông tin người mua vàng. Thượng tá Lê Mạnh Hà - Phó Trưởng Phòng Tham mưu Công an TP.HCM cho biết việc thu thập thông tin người mua bán vàng nhằm ngăn chặn việc đầu cơ và đảm bảo yêu cầu bí mật của người dân theo quy định. Công an TP.HCM cùng Ngân hàng Nhà nước và các ngành chức năng thành lập tổ công tác đảm bảo an ninh thị trường vàng, không phải kiểm tra hay làm khó, mà bảo vệ quyền lợi chính đáng của người dân, doanh nghiệp chế tác, ngăn chặn tình trạng đầu cơ, lợi dụng giá vàng lên cao để trục lợi. "Tôi khẳng định các thông tin trao đổi giữa các cơ quan luôn đảm bảo yêu cầu bí mật của người dân theo quy định. Việc khai thác sử dụng thông tin cũng đảm bảo quy định Nhà nước và quy định về bảo mật thông tin", Thượng tá Lê Mạnh

In [48]:
txt_p = convertData(txt)
txt_e = model.encode(txt_p)

In [49]:
svc_model_ebd.predict([text_ebd])

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but SVC was fitted with feature names
  warnings.warn(


array([1])

In [ ]:
X_bert = pd.concat([ebd_teptinthat,ebd_teptingia])
y_bert = [1]*len(ebd_teptinthat) + [0]*len(ebd_teptingia)
X_bert.reset_index(inplace=True)
X_bert.drop(columns=['index'],inplace=True)

In [ ]:
X_train_b, X_test_b, y_train_b, y_test_b = train_test_split(X_bert, y_bert, test_size=0.2, random_state=42)

In [ ]:
svc_model_ebd = SVC(kernel='linear', C=1)

In [ ]:
svc_model_ebd.fit(X_train_b, y_train_b)

SVC(C=1, kernel='linear')

In [ ]:
y_pred = svc_model_ebd.predict(X_test_b)
#kiểm tra X_test_tfidf
# Calculate the accuracy of the model.
accuracy = accuracy_score(y_test_b, y_pred)
print("Accuracy: {:.2f}%".format(accuracy * 100))
# Display the classification report and confusion matrix.
print("Classification Report:")
print(classification_report(y_test_b, y_pred))
print("Confusion Matrix:")
print(confusion_matrix(y_test_b, y_pred))

Accuracy: 98.88%
Classification Report:
              precision    recall  f1-score   support

           0       0.99      0.99      0.99       819
           1       0.99      0.99      0.99       970

    accuracy                           0.99      1789
   macro avg       0.99      0.99      0.99      1789
weighted avg       0.99      0.99      0.99      1789

Confusion Matrix:
[[810   9]
 [ 11 959]]


In [ ]:
joblib.dump(svc_model_ebd, '/content/drive/MyDrive/SIC/svc_model_ebd.pkl')

['/content/drive/MyDrive/SIC/svc_model_ebd.pkl']

In [ ]:
knn_model_ebd = KNeighborsClassifier(n_neighbors=5)
knn_model_ebd.fit(X_train_b, y_train_b)

KNeighborsClassifier()

In [31]:
knn_model_ebd = joblib.load('/content/drive/MyDrive/SIC/knn_model_ebd.pkl')

In [45]:
text=input()
txt_e = convertData(txt)
text_ebd = model.encode(txt_e)

Công an TP.HCM: Thu thập thông tin người mua bán vàng nhằm ngăn chặn việc đầu cơ Báo Người Lao Động đưa tin, chiều 1/8, UBND TP.HCM tổ chức họp báo tình hình kinh tế - xã hội trên địa bàn. Tại buổi họp báo, đại diện Công an TP.HCM đã thông tin về việc thu thập thông tin người mua vàng. Thượng tá Lê Mạnh Hà - Phó Trưởng Phòng Tham mưu Công an TP.HCM cho biết việc thu thập thông tin người mua bán vàng nhằm ngăn chặn việc đầu cơ và đảm bảo yêu cầu bí mật của người dân theo quy định. Công an TP.HCM cùng Ngân hàng Nhà nước và các ngành chức năng thành lập tổ công tác đảm bảo an ninh thị trường vàng, không phải kiểm tra hay làm khó, mà bảo vệ quyền lợi chính đáng của người dân, doanh nghiệp chế tác, ngăn chặn tình trạng đầu cơ, lợi dụng giá vàng lên cao để trục lợi. "Tôi khẳng định các thông tin trao đổi giữa các cơ quan luôn đảm bảo yêu cầu bí mật của người dân theo quy định. Việc khai thác sử dụng thông tin cũng đảm bảo quy định Nhà nước và quy định về bảo mật thông tin", Thượng tá Lê Mạnh

In [46]:
knn_model_ebd.predict([text_ebd])

/usr/local/lib/python3.10/dist-packages/sklearn/base.py:465: UserWarning: X does not have valid feature names, but KNeighborsClassifier was fitted with feature names
  warnings.warn(


array([0])

In [ ]:
y_pred = knn_model_ebd.predict(X_test_b)
#kiểm tra X_test_tfidf
# Calculate the accuracy of the model.
accuracy = accuracy_score(y_test_b, y_pred)
print("Accuracy: {:.2f}%".format(accuracy * 100))
# Display the classification report and confusion matrix.
print("Classification Report:")
print(classification_report(y_test_b, y_pred))
print("Confusion Matrix:")
print(confusion_matrix(y_test_b, y_pred))

Accuracy: 83.73%
Classification Report:
              precision    recall  f1-score   support

           0       0.77      0.91      0.84       819
           1       0.91      0.77      0.84       970

    accuracy                           0.84      1789
   macro avg       0.84      0.84      0.84      1789
weighted avg       0.85      0.84      0.84      1789

Confusion Matrix:
[[749  70]
 [221 749]]


In [ ]:
joblib.dump(knn_model_ebd, '/content/drive/MyDrive/SIC/knn_model_ebd.pkl')

['/content/drive/MyDrive/SIC/knn_model_ebd.pkl']

In [ ]:
# y_pred = knn_model.predict(X_test)
# # Calculate the accuracy of the model.
# accuracy = accuracy_score(y_test, y_pred)
# print("Accuracy: {:.2f}%".format(accuracy * 100))
# # Display the classification report and confusion matrix.
# print("Classification Report:")
# print(classification_report(y_test, y_pred))
# print("Confusion Matrix:")
# print(confusion_matrix(y_test, y_pred))
# #bỏ KMeans

#Vẽ kết quả

In [ ]:
# cs = lt[0]
# models = ['Cosine','SVC', 'KNN']  # Tên các mô hình
# scores = [cs, 0.9504, 0.64]  # Tỉ số của từng mô hình

# Thiết lập vị trí cho các cột
x = np.arange(len(models))

plt.figure(figsize=(10, 6))

# Vẽ biểu đồ cột
plt.bar(x, scores, color=['blue', 'orange', 'green', 'red'], alpha=0.7)
# Thêm nhãn cho các trục và tiêu đề
plt.xticks(x, models)
plt.ylim(0, 1)
plt.xlabel('Mô Hình')
plt.ylabel('Độ chính xác')
plt.title('Đánh giá độ chính xác của Các Mô Hình và kỹ thuật')
plt.grid(axis='y')  # Thêm lưới cho trục y
#Giữ nguyên kết quả tfidf
#bổ sung thêm với thực nghiệm sentence_transformer
#Bỏ Kmeans

In [ ]:
cs = lt[0]
# models = ['Cosine','SVC', 'KNN']  # Tên các mô hình
# scores = [cs, 0.9504, 0.64]  # Tỉ số của từng mô hình

# Thiết lập vị trí cho các cột
# x = np.arange(len(models))

plt.figure(figsize=(10, 6))

# Vẽ biểu đồ cột
# plt.bar(x, scores, color=['blue', 'orange', 'green', 'red'], alpha=0.7)
plt.bar(x='m',height=lt[0],color='red',alpha=0.7)
plt.bar(x='m',height=lt[1],color='orange',alpha=0.7)

# Thêm nhãn cho các trục và tiêu đề
# plt.xticks(x, models)
plt.ylim(0, 1)
plt.xlim(0,5)
plt.legend(['Cosine_tfidf','Cosine_ebd'])
plt.xlabel('Mô Hình')
plt.ylabel('Độ chính xác')
plt.title('Đánh giá độ chính xác của Các Mô Hình và kỹ thuật')
plt.grid(axis='y')  # Thêm lưới cho trục y
#Giữ nguyên kết quả tfidf
#bổ sung thêm với thực nghiệm sentence_transformer
#Bỏ Kmeans